# Exploratory Analysis of RV Rental Listings in the US

## Step 1: Import packages and load csv data into Pandas dataframe

In [228]:
# import necessary packages

import pandas as pd
import numpy as np
import re
import plotly.express as px

In [229]:
# Read csv files into dataframe objects and merge into single dataframe

df1 = pd.read_csv('./rvshare_0to5.csv')
df2 = pd.read_csv('./rvshare_5to10.csv')
df3 = pd.read_csv('./rvshare_10to15.csv')
df4 = pd.read_csv('./rvshare_15to20.csv')
df5 = pd.read_csv('./rvshare_20to23.csv')
df = pd.concat([df1,df2,df3,df4,df5])



# Set pandas display options
pd.set_option('display.max_columns',None)
# pd.set_option('display.min_rows',0)
# pd.set_option('display.max_rows',None)

## Step 2: Transform columns into desired types and remove outliers

In [230]:
# Transform dataframe columns(features) into correct dtypes
# Code on this cell will throw error if it had already run after import since datatype is already changed


# Convert types
# Convert 'price_nightly', 'price_weekly', and 'price_monthly' from string to float types
df['price_nightly'] = df['price_nightly'].str.replace('$','').str.replace(',','').astype(float)
df['price_weekly'] = df['price_weekly'].str.replace('$','').str.replace(',','').astype(float)
df['price_monthly'] = df['price_monthly'].str.replace('$','').str.replace(',','').astype(float)

# Convert 'cancellation'(string) to (int) by assigning Flexible: 1, Standard: 2, Strict: 3.
# df.cancellation = df.cancellation.str.replace('Flexible','1').str.replace('Standard','2').str.replace('Strict','3').astype(int)

# Convert 'length'(string) to (int)
df['length'] = pd.to_numeric(df['length'].str.replace('ft',''),errors='coerce')



# Create new features
# Create feature 'distance_to_city'(float) by extracting number from 'distance' feature.
df['distance_to_city'] = df['distance'].str.findall('(\d*\.?\d*) miles from')
df['distance_to_city'] = pd.to_numeric(df['distance_to_city'].apply(lambda x: x[0]), errors='coerce')

# Create 'major_state'(string) and 'major city'(string) features from 'distance' feature
df['major_city'] = df.distance.str.findall('miles from (\D+)').map(lambda x: x[0]).str.split(',').map(lambda x: x[0].strip())
df['major_state'] = df.distance.str.findall('miles from (\D+)').map(lambda x: x[0]).str.split(',').map(lambda x: x[1].strip())

# Split 'bathroom' feature to separate (bool) features
df['shower_yn']=df.bathroom.str.lower().str.contains('shower').fillna(False)
df['toilet_yn']=df.bathroom.str.lower().str.contains('toilet').fillna(False)
df['bathroom_sink_yn']=df.bathroom.str.lower().str.contains('sink').fillna(False)

# Split 'entertainment' feature to separate (bool) feature
df['tv_yn']=df.entertainment.str.lower().str.contains('tv').fillna(False)

# Split 'kitchen' feature to separate (bool) features
df['refrigerator_yn']=df.kitchen.str.lower().str.contains('refrigerator').fillna(False)
df['microwave_yn']=df.kitchen.str.lower().str.contains('microwave').fillna(False)
df['kitchen_sink_yn']=df.kitchen.str.lower().str.contains('sink').fillna(False)
df['stove_yn']=df.kitchen.str.lower().str.contains('stove').fillna(False)

# Split 'temperature_control' feature to separate (bool) features
df['air_conditioning_yn']=df.temperature_control.str.lower().str.contains('air conditioning').fillna(False)
df['hot_water_yn']=df.temperature_control.str.lower().str.contains('hot & cold water').fillna(False)

# Drop processed columns
df = df.drop(columns = ['bathroom','distance','entertainment','kitchen','temperature_control'])


# Drop rows with price_nightly > $3,000
df.drop(df[df['price_nightly'] > 1000].index, inplace = True)
df.drop(df[df['year'] < 1940].index, inplace = True)

df

cancellation  length          location  \
0        Flexible   33.00     Shoreline, WA   
1        Flexible   36.00  Port Orchard, WA   
2        Standard   21.00    Mill Creek, WA   
3        Standard   20.00        Auburn, WA   
4        Standard   32.00       Seattle, WA   
...           ...     ...               ...   
1667     Standard   19.00      Capitola, CA   
1668     Standard   24.00          Lodi, CA   
1669     Flexible   23.92   Suisun City, CA   
1670       Strict   25.00       Vallejo, CA   
1671     Standard   36.00      San Jose, CA   

                                             name  price_monthly  \
0                    2006 Jayco Jayflight 31 BHDS         1990.0   
1                            2014 Coachman Mirada         4999.0   
2                2018 Venture Sonic Lite SL169VBH         2550.0   
3        Perfect beginner camper for small family         3600.0   
4                  Tioga Infinity... and beyond!!         3500.0   
...                                           ...            ...   
1667            2014 Airstream RV Flying Cloud 19         2525.0   
1668                            The Camping Truck         5460.0   
1669  2016 Forest River Coachmen Freelander 21...         5100.0   
1670  Mercedes Benz - Coachmen Prism 2150LE (D...         4950.0   
1671             2019 Elkridge Extreme Light e326         4199.0   

      price_nightly  price_weekly  \
0              95.0         520.0   
1             199.0        1299.0   
2             105.0         650.0   
3             150.0         900.0   
4             165.0         900.0   
...             ...           ...   
1667           99.0         624.0   
1668          195.0        1365.0   
1669          175.0        1190.0   
1670          195.0        1290.0   
1671          169.0        1099.0   

                                             rv_details  sleeps  \
0     Year - 2006,Manufacturer - Jayco,Make - Jay Fl...       8   
1     Year - 2014,Manufacturer - Coachmen RV,Make - ...       4   
2     Year - 2018,Manufacturer - Venture RV,Make - S...       4   
3     Year - 2020,Manufacturer - Forest River RV,Mak...       4   
4     Year - 2008,Manufacturer - Fleetwood RV,Make -...       8   
...                                                 ...     ...   
1667  Year - 2014,Manufacturer - Airstream RV,Make -...       4   
1668  Year - 2016,Manufacturer - Thor Motor Coach,Ma...       5   
1669  Year - 2016,Manufacturer - Forest River,Make -...       5   
1670  Year - 2016,Manufacturer - Coachmen RV,Make - ...       6   
1671  Year - 2019,Manufacturer - Heartland,Make - El...       9   

            vehicle_type  year  distance_to_city major_city major_state  \
0         Travel Trailer  2006              11.7    Seattle          WA   
1     Class A Motor Home  2014              17.9    Seattle          WA   
2         Travel Trailer  2018              18.9    Seattle          WA   
3         Travel Trailer  2020              18.5    Seattle          WA   
4     Class C Motor Home  2008               9.4    Seattle          WA   
...                  ...   ...               ...        ...         ...   
1667      Travel Trailer  2014              25.5   San Jose          CA   
1668  Class C Motor Home  2016              64.2   San Jose          CA   
1669  Class C Motor Home  2016              64.1   San Jose          CA   
1670  Class C Motor Home  2016              58.7   San Jose          CA   
1671         Fifth Wheel  2019               5.8   San Jose          CA   

      shower_yn  toilet_yn  bathroom_sink_yn  tv_yn  refrigerator_yn  \
0          True       True              True   True             True   
1          True       True              True   True             True   
2          True       True              True  False             True   
3          True       True              True   True             True   
4          True       True              True   True             True   
...         ...        ...              

## Step 3: Explore various dimensions of the clean dataset

In [279]:
# First let's take a look at the year and type of vehicles in our dataset

fig = px.line(df.groupby('year').count().reset_index(), x='year', y='name', labels={'name':'Number of Listings', 'year':'Year'}, title = 'Number of Listings per Year')
fig.show()

fig = px.bar(df.groupby('vehicle_type').count().reset_index(), x='vehicle_type', y='name', labels={'name':'Number of Listings', 'vehicle_type': 'RV Type'}, title = 'Number of Listings per RV Type')
fig.show()

fig = px.histogram(df.price_nightly, nbins = 75, labels = {'value': "Nightly Price"}, title = 'Distribution of Nightly Price')
fig.show()

The first graph shows that the biggest percentage of listings come from vehicles produced in 2018. It is not common to see vehicles made before 2002. This can also mean that the lifespan of an RV to be rented out is around 18 years.

The second graph shows the spread of listings by RT type. Travel Trailers were the most common and folding trailers were the least common.

In [288]:
# box plot to show distribution of price per year and vehicle type

fig = px.box(df, x='year', y='price_nightly', labels={'price_nightly':'Price Nightly', 'year':'Year'}, title = 'Box Plots of Nightly Price per Year')
fig.show()

fig = px.line(x=df.groupby('year').median().reset_index().sort_values('year')['year'], y=df.groupby('year').median().reset_index().sort_values('year')['price_nightly'], labels={'price_nightly':'Price Nightly', 'year':'Year'}, title = 'Median Nightly Price per Year')
fig.show()

# only for travel trailers
# fig = px.line(x=df[df.vehicle_type =='Travel Trailer'].groupby('year').median().reset_index().sort_values('year')['year'], y=df[df.vehicle_type =='Travel Trailer'].groupby('year').median().reset_index().sort_values('year')['price_nightly'], labels={'price_nightly':'Price Nightly', 'year':'Year'}, title = 'Median Nightly Price per Year')
# fig.show()


fig = px.box(df, x='vehicle_type', y='price_nightly', labels={'price_nightly':'Price Nightly', 'vehicle_type': 'RV Type'}, title = 'Distribution of Nightly Price per RV Type')
fig.show()

In [271]:
# Investigate the effect of having certain features on price

# fig = px.bar(df.groupby('shower_yn').median().reset_index(), x='shower_yn', y='price_nightly', labels={'shower_yn':'Has Shower', 'price_nightly': 'Nightly Price'}, title = 'Median Nightly Price for Listings With and Without Shower')
# fig.show()

# print(df.groupby('shower_yn').median().reset_index()[['shower_yn','price_nightly']])
# print(df.groupby('toilet_yn').median().reset_index()[['toilet_yn','price_nightly']])
# print(df.groupby('bathroom_sink_yn').median().reset_index()[['bathroom_sink_yn','price_nightly']])
# print(df.groupby('tv_yn').median().reset_index()[['tv_yn','price_nightly']])
# print(df.groupby('refrigerator_yn').median().reset_index()[['refrigerator_yn','price_nightly']])
# print(df.groupby('microwave_yn').median().reset_index()[['microwave_yn','price_nightly']])
# print(df.groupby('kitchen_sink_yn').median().reset_index()[['kitchen_sink_yn','price_nightly']])
# print(df.groupby('stove_yn').median().reset_index()[['stove_yn','price_nightly']])
# print(df.groupby('air_conditioning_yn').median().reset_index()[['air_conditioning_yn','price_nightly']])
# print(df.groupby('hot_water_yn').median().reset_index()[['hot_water_yn','price_nightly']])

df_feature_diff = pd.DataFrame([['Shower', 15],
                                ['Toilet', 15],
                                ['Bathroom_Sink', 35],
                                ['TV', 30],
                                ['Refrigerator', 0],
                                ['Microwave', 10],
                                ['Kitchen_Sink', -1],
                                ['Stove', 0],
                                ['AC', 15],
                                ['Hot Water', 15]], 
                               columns=['Feature','Difference in Price'])
fig = px.bar(x=df_feature_diff.sort_values('Difference in Price').Feature, y=df_feature_diff.sort_values('Difference in Price')['Difference in Price'], labels = {'x':'Feature', 'y':'Price Increase'}, title = 'Price Increase per Feature')
fig.show()

In [248]:
# Investigate effect of distance from major city on price_nightly
# shows no correlation
fig = px.scatter(x=df.distance_to_city, y=df.price_nightly)
# fig.show()

# lets try separating by vehicle type
# still no correlation

# fig = px.scatter(x = df[df.vehicle_type == 'Travel Trailer'].distance_to_city, y = df[df.vehicle_type == 'Travel Trailer'].price_nightly)
# fig.show()

# fig = px.scatter(x = df[(df.vehicle_type == 'Travel Trailer')&(df.price_nightly<200)].distance_to_city, y = df[(df.vehicle_type == 'Travel Trailer')&(df.price_nightly<200)].price_nightly)
# fig.show()

fig = px.scatter(x = df[(df.vehicle_type == 'Class A Motor Home')&(df.price_nightly<200)].distance_to_city, y = df[(df.vehicle_type == 'Class A Motor Home')&(df.price_nightly<200)].price_nightly, trendline = 'ols')
fig.show()



In [306]:
# Investigate how much money you save per night by booking weekly and monthly
df['Monthly_Booking']=df.price_monthly/30.5
df['Weekly_Booking']=df.price_weekly/7
fig = px.bar(df[['price_nightly','Weekly_Booking','Monthly_Booking']].median().reset_index(), x='index', y=0, labels={'0':'Nightly Price', 'index':'Booking Type'}, title = 'Median Price per Booking Type')
fig.show()

In [239]:
# Investigate price for cancellation type
fig = px.bar(df.groupby('cancellation')['price_nightly'].median().reset_index(), x='cancellation', y='price_nightly', labels={'cancellation':'Cancellation Type', 'price_nightly':'Price per Night'}, title = 'Median Price per Cancellation Type')
fig.show()

In [298]:
# Investigate the effect of length of vehicle on price (grouped by vehicle type)

# fig = px.histogram(df[df.vehicle_type == 'Travel Trailer'], x = 'length', y= 'price_nightly', histfunc='avg')
# fig.show()

fig = px.scatter(x= df[df.vehicle_type == 'Travel Trailer'].length, y=df[df.vehicle_type == 'Travel Trailer'].price_nightly, trendline = 'ols', labels = {'x':'Length of Vehicle','y':'Nightly Price'}, title = 'Effect of Length of Vehicle on Price (Travel Trailers)')
fig.show()

fig = px.scatter(x= df.length, y=df.price_nightly, trendline = 'ols', labels = {'x':'Length of Vehicle','y':'Nightly Price'}, title = 'Effect of Length of Vehicle on Price')
fig.show()

## Step 4: Additional analysis after merging 2017 state income dataset

In [305]:
# Investigate the correlation between median income per state and price_nightly
# processing median income per state (2017) dataset to merge
df_income = pd.read_csv('./median_income_2017.csv')

us_state_abbrev = {
'Alabama': 'AL', 'Alaska': 'AK', 'Arizona': 'AZ', 'Arkansas': 'AR', 'California': 'CA', 'Colorado': 'CO',
'Connecticut': 'CT', 'Delaware': 'DE', 'Florida': 'FL', 'Georgia': 'GA', 'Hawaii': 'HI', 'Idaho': 'ID',
'Illinois': 'IL', 'Indiana': 'IN', 'Iowa': 'IA', 'Kansas': 'KS', 'Kentucky': 'KY', 'Louisiana': 'LA',
'Maine': 'ME', 'Maryland': 'MD', 'Massachusetts': 'MA', 'Michigan': 'MI', 'Minnesota': 'MN', 'Mississippi': 'MS',
'Missouri': 'MO', 'Montana': 'MT', 'Nebraska': 'NE', 'Nevada': 'NV', 'New Hampshire': 'NH', 'New Jersey': 'NJ',
'New Mexico': 'NM', 'New York': 'NY', 'North Carolina': 'NC', 'North Dakota': 'ND', 'Ohio': 'OH', 'Oklahoma': 'OK',
'Oregon': 'OR', 'Pennsylvania': 'PA', 'Rhode Island': 'RI', 'South Carolina': 'SC', 'South Dakota': 'SD',
'Tennessee': 'TN', 'Texas': 'TX', 'Utah': 'UT', 'Vermont': 'VT', 'Virginia': 'VA', 'Washington': 'WA',
'West Virginia': 'WV', 'Wisconsin': 'WI', 'Wyoming': 'WY'}


df_income['State'] = df_income['State'].map(us_state_abbrev).fillna(df_income['State'])
df_income['2017'] = pd.to_numeric(df_income['2017'].str.replace(',',''), errors='coerce')

df_price_state = df[['price_nightly', 'major_state']].groupby('major_state').median().sort_values('price_nightly').reset_index()
df_income_price_state = pd.merge(df_price_state, df_income[['State','2017']], how='inner', left_on ='major_state', right_on='State')

fig = px.scatter(df_income_price_state, x='2017', y='price_nightly',trendline="ols", labels = {'2017': 'Median Income (2017)', 'price_nightly':'Nightly Price'}, title = 'Effect of Median Income of State on Price')
fig.show()

In [8]:
city_urls = ['https://rvshare.com/rv-rental/las-vegas/nv',
 'https://rvshare.com/rv-rental/denver/co',
 'https://rvshare.com/rv-rental/los-angeles/ca',
 'https://rvshare.com/rv-rental/san-diego/ca',
 'https://rvshare.com/rv-rental/seattle/wa',
 'https://rvshare.com/rv-rental/austin/tx',
 'https://rvshare.com/rv-rental/dallas/tx',
 'https://rvshare.com/rv-rental/salt-lake-city/ut',
 'https://rvshare.com/rv-rental/anchorage/ak',
 'https://rvshare.com/rv-rental/chicago/il',
 'https://rvshare.com/rv-rental/sacramento/ca',
 'https://rvshare.com/rv-rental/atlanta/ga',
 'https://rvshare.com/rv-rental/boise/id',
 'https://rvshare.com/rv-rental/san-francisco/ca',
 'https://rvshare.com/rv-rental/reno/nv',
 'https://rvshare.com/rv-rental/new-york/ny',
 'https://rvshare.com/rv-rental/orlando/fl',
 'https://rvshare.com/rv-rental/san-antonio/tx',
 'https://rvshare.com/rv-rental/spokane/wa',
 'https://rvshare.com/rv-rental/kansas-city/mo',
 'https://rvshare.com/rv-rental/san-jose/ca',
 'https://rvshare.com/rv-rental/phoenix/az',
 'https://rvshare.com/rv-rental/st-louis/mo']

# rvshare_0to5.csv
for i in city_urls[0:5]:
    print(i)
print('='*50)
    
# rvshare_5to10.csv
for i in city_urls[5:10]:
    print(i)
print('='*50)

# rvshare_10to15.csv
for i in city_urls[10:15]:
    print(i)
print('='*50)    

for i in city_urls[15:20]:
    print(i)
print('='*50)    

for i in city_urls[20:]:
    print(i)
print('='*50)

https://rvshare.com/rv-rental/las-vegas/nv
https://rvshare.com/rv-rental/denver/co
https://rvshare.com/rv-rental/los-angeles/ca
https://rvshare.com/rv-rental/san-diego/ca
https://rvshare.com/rv-rental/seattle/wa
https://rvshare.com/rv-rental/austin/tx
https://rvshare.com/rv-rental/dallas/tx
https://rvshare.com/rv-rental/salt-lake-city/ut
https://rvshare.com/rv-rental/anchorage/ak
https://rvshare.com/rv-rental/chicago/il
https://rvshare.com/rv-rental/sacramento/ca
https://rvshare.com/rv-rental/atlanta/ga
https://rvshare.com/rv-rental/boise/id
https://rvshare.com/rv-rental/san-francisco/ca
https://rvshare.com/rv-rental/reno/nv
https://rvshare.com/rv-rental/new-york/ny
https://rvshare.com/rv-rental/orlando/fl
https://rvshare.com/rv-rental/san-antonio/tx
https://rvshare.com/rv-rental/spokane/wa
https://rvshare.com/rv-rental/kansas-city/mo
https://rvshare.com/rv-rental/san-jose/ca
https://rvshare.com/rv-rental/phoenix/az
https://rvshare.com/rv-rental/st-louis/mo
